In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
# for dirname, _, filenames in os.walk('/kaggle/input'):
#     for filename in filenames:
#         print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [2]:
!pip install datasets peft torch torchvision 

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 29.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 13.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 88.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 kB 10.3 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.9.41
    Uninstalling nvidia-nvjitlink-cu12-12.9.41:
      Successfully uninstalled nvidia-nvjitlink-cu12-12.9.41
  Attempting uninstall: nvidia-curand-cu12
    Found existing installation: nvidia-curand-cu12 10.3.10.19
    Uninstalling nvidia-curand-cu12-

In [3]:
!pip install -q transformers torch evaluate scikit-learn pillow

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.0/84.0 kB 3.0 MB/s eta 0:00:00


In [4]:
import os
import sys
import subprocess

# 1️⃣ Uninstall any existing bitsandbytes build
#    to avoid mismatched CUDA binaries
print("🎯 Uninstalling old bitsandbytes...")
subprocess.run([sys.executable, "-m", "pip", "uninstall", "-y", "bitsandbytes"], check=True)

# 2️⃣ Install bitsandbytes >=0.43.2 which adds upstream support for CUDA 12.4+
#    (see HF docs: supports CUDA 11.0–12.5, including 12.4+) :contentReference[oaicite:0]{index=0}
print("🎯 Installing bitsandbytes>=0.43.2 for CUDA 12.4 support...")
subprocess.run([sys.executable, "-m", "pip", "install", "--upgrade", "bitsandbytes>=0.43.2"], check=True)

# 3️⃣ Ensure the CUDA 12.4 runtime path is on LD_LIBRARY_PATH
#    so bitsandbytes can locate libcudart and its own libbitsandbytes_cuda124 :contentReference[oaicite:1]{index=1}
cuda_lib="/usr/local/cuda-12.4/lib64"
prev_ld = os.environ.get("LD_LIBRARY_PATH", "")
os.environ["LD_LIBRARY_PATH"] = f"{cuda_lib}:{prev_ld}"
print(f"🎯 LD_LIBRARY_PATH set to include {cuda_lib}")

# 4️⃣ Restart prompt reminder (mandatory in Colab to pick up the new .so files)
#    In standalone scripts this is not needed, but in notebooks you must restart runtime.
print("\n⚠️  If you’re in a Colab notebook, **please restart the runtime now**\n    (Runtime → Restart runtime) and re-run this cell/script.\n")

# 5️⃣ Diagnostic: confirm bitsandbytes is seeing CUDA 12.4
print("🔍 Running bitsandbytes diagnostic...")
res = subprocess.run([sys.executable, "-m", "bitsandbytes"], capture_output=True, text=True)
print(res.stdout)
if "CUDA" not in res.stdout:
    raise RuntimeError("bitsandbytes did not detect CUDA—check your LD_LIBRARY_PATH and installation.")


🎯 Uninstalling old bitsandbytes...


🎯 Installing bitsandbytes>=0.43.2 for CUDA 12.4 support...
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.1/76.1 MB 24.7 MB/s eta 0:00:00
🎯 LD_LIBRARY_PATH set to include /usr/local/cuda-12.4/lib64

⚠️  If you’re in a Colab notebook, **please restart the runtime now**
    (Runtime → Restart runtime) and re-run this cell/script.

🔍 Running bitsandbytes diagnostic...
++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++
++++++++++++++++++ BUG REPORT INFORMATION ++++++++++++++++++
++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++
++++++++++++++++++++++++++ OTHER +++++++++++++++++++++++++++
CUDA specs: CUDASpecs(highest_compute_capability=(6, 0), cuda_version_string='124', cuda_version_tuple=(12, 4))
PyTorch settings found: CUDA_VERSION=124, Highest Compute Capability: (6, 0).
To manually override the PyTorch CUDA version please see: https://github.com/TimDettmers/bitsandbytes/blob/main/docs/source/nonpytorchcuda.mdx
If you run into issues with 8-bit matmul, you can try 4

In [5]:
import os
import ast
import pandas as pd
from PIL import Image
import torch
from sklearn.model_selection import train_test_split  # scikit-learn split :contentReference[oaicite:2]{index=2}
import evaluate                                        # metrics :contentReference[oaicite:3]{index=3}
from transformers import AutoProcessor, AutoModelForVision2Seq , BitsAndBytesConfig, get_linear_schedule_with_warmup, Seq2SeqTrainingArguments, Seq2SeqTrainer, DataCollatorForSeq2Seq
from peft import prepare_model_for_kbit_training, LoraConfig, get_peft_model, PeftModel, TaskType
from datasets import Dataset

CSV_PATH = "/kaggle/input/images-with-vqas/train_80.csv"
train_df = pd.read_csv(CSV_PATH)

train_df["image_path"] = train_df["image_path"].str.replace(
    r"^Dataset/final_dataset/",
    "/kaggle/input/images-with-vqas/final_dataset/final_dataset/",
    regex=True
)

train_df["vqa_response"] = train_df["vqa_response"].apply(ast.literal_eval)
train_df = train_df.explode("vqa_response").reset_index(drop=True)
train_df[["question", "answer"]] = pd.DataFrame(train_df["vqa_response"].tolist(), index=train_df.index)

exists = train_df["image_path"].apply(os.path.exists)
print(f"Skipping {(~exists).sum()} rows with missing images")
train_df = train_df[exists]

train_df = train_df[["image_path", "question", "answer"]].reset_index(drop=True)
print(f"Total examples: {len(train_df)}")

2025-05-15 13:23:51.071133: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1747315431.253569      19 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1747315431.308682      19 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


Skipping 0 rows with missing images
Total examples: 46504


In [6]:
CSV_PATH = "/kaggle/input/images-with-vqas/test.csv"
test_df = pd.read_csv(CSV_PATH)

test_df["image_path"] = test_df["image_path"].str.replace(
    r"^Dataset/final_dataset/",
    "/kaggle/input/images-with-vqas/final_dataset/final_dataset/",
    regex=True
)

test_df["vqa_response"] = test_df["vqa_response"].apply(ast.literal_eval)
test_df = test_df.explode("vqa_response").reset_index(drop=True)
test_df[["question", "answer"]] = pd.DataFrame(test_df["vqa_response"].tolist(), index=test_df.index)

exists = test_df["image_path"].apply(os.path.exists)
print(f"Skipping {(~exists).sum()} rows with missing images")
test_df = test_df[exists]

test_df = test_df[["image_path", "question", "answer"]].reset_index(drop=True)
print(f"Total examples: {len(test_df)}")

Skipping 0 rows with missing images
Total examples: 29047


In [7]:
import os
import pandas as pd
from PIL import Image
from transformers import AutoProcessor, AutoModelForVisualQuestionAnswering, Trainer, TrainingArguments
import torch
from accelerate import Accelerator
from sklearn.model_selection import train_test_split
from peft import LoraConfig, get_peft_model
from transformers.data.data_collator import default_data_collator
from transformers import Blip2ForConditionalGeneration, Blip2Processor, AutoModelForVision2Seq
# Initialize Accelerator for efficient multi-GPU training
# accelerator = Accelerator()

quantization_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_compute_dtype=torch.float16,
    bnb_4bit_quant_type="nf4",
)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_id ="Salesforce/blip2-opt-2.7b"
base_model = AutoModelForVision2Seq.from_pretrained(
    model_id,
    # load_in_4bit=True,
    quantization_config=quantization_config,
    device_map = "auto"
)

processor = AutoProcessor.from_pretrained(model_id)
if processor.tokenizer.pad_token is None:
    processor.tokenizer.pad_token = processor.tokenizer.eos_token

config.json:   0%|          | 0.00/1.03k [00:00<?, ?B/s]

model.safetensors.index.json:   0%|          | 0.00/122k [00:00<?, ?B/s]

Fetching 2 files:   0%|          | 0/2 [00:00<?, ?it/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/10.0G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/4.98G [00:00<?, ?B/s]

...

vocab.json:   0%|          | 0.00/798k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/3.56M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/23.0 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/548 [00:00<?, ?B/s]

In [8]:
# model   = PeftModel.from_pretrained(
#                    base_model, 
#                    "/kaggle/input/blip2-lora-finetuned/pytorch/default/1/blip2_finetuned/checkpoint-561/")  # same folder you saved earlier

# model.to(device).eval()

In [9]:
from tqdm import tqdm
preds, refs = [], []
count=0
for row in tqdm(test_df.itertuples(), total = len(test_df)):
    img = Image.open(row.image_path).convert("RGB")
    prompt = f"Based on the image, answer the following question with a single word. Question: {row.question} Answer:"
    inputs = processor(images=img, text=prompt, return_tensors="pt").to(device)
    pixel_values   = inputs["pixel_values"]
    input_ids      = inputs["input_ids"]
    attention_mask = inputs["attention_mask"]
    out = base_model.generate(
        pixel_values=pixel_values,
        input_ids=input_ids,
        attention_mask=attention_mask,
        max_new_tokens=10
    )
    text = processor.batch_decode(out, skip_special_tokens=True)[0].strip()
    # print("text:",text)
    pred = text.split()[-1].rstrip(".,;:!?") if text else ""
    preds.append(pred.lower())
    refs.append(row.answer.lower())
    print("prediction: ",pred.lower())
    print("reference: ",row.answer.lower())
    count+=1
    # if count==100:
    #     break

  0%|          | 1/29047 [00:01<11:48:46,  1.46s/it]

prediction:  brown
reference:  brown


  0%|          | 2/29047 [00:01<6:13:01,  1.30it/s] 

prediction:  leather
reference:  leather


  0%|          | 3/29047 [00:02<4:23:36,  1.84it/s]

...

prediction:  blue
reference:  blue


100%|█████████▉| 29046/29047 [2:30:13<00:00,  3.38it/s]

prediction:  blue
reference:  green


100%|██████████| 29047/29047 [2:30:13<00:00,  3.22it/s]

prediction:  flexible
reference:  yes


In [10]:
# ──────────────────────────────────────────────────────────────────────────────
# 6. Compute Metrics (and identify mismatches)
# ──────────────────────────────────────────────────────────────────────────────
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
import evaluate
# from bert_score import BERTScorer # Keep if you add BERTScore later
# from rouge_score import rouge_scorer # Keep if you add ROUGE later
# from rapidfuzz.distance import Levenshtein # Keep if you add Levenshtein later
from sentence_transformers import SentenceTransformer, util # Keep if you add SBERT later
import numpy as np
import pandas as pd # Ensure pandas is imported if df is used



# normalize case
preds_l = [str(p).lower().strip() for p in preds] # Added str() and strip() for robustness
refs_l  = [str(r).lower().strip() for r in refs]   # Added str() and strip()

# # 1) TOKEN-LEVEL EXACT MATCH → binary labels
y_pred_bin = [int(p == r) for p, r in zip(preds_l, refs_l)]
y_true_bin = [1]*len(refs_l)            # reference is always “correct” class

acc = accuracy_score(y_true_bin, y_pred_bin)
prec, rec, f1, _ = precision_recall_fscore_support(
    y_true_bin, y_pred_bin, average="binary", zero_division=0
)
print(f"Exact-match Accuracy: {acc:.3f}")
print(f"Exact-match Precision: {prec:.3f}") # Will be 1.0 if acc > 0, else 0.0
print(f"Exact-match Recall:    {rec:.3f}")    # Will be same as acc
print(f"Exact-match F1:        {f1:.3f}\n")  

Exact-match Accuracy: 0.508
Exact-match Precision: 1.000
Exact-match Recall:    0.508
Exact-match F1:        0.674

